# Deliverable 3. Create a Travel Itinerary Map

----

1. Create a folder called `Vacation_Itinerary` to store all the files for this deliverable.

2. Download the `Vacation_Itinerary_starter_code.ipynb` file into your `Vacation_Itinerary` folder and rename it `Vacation_Itinerary.ipynb`.

3. Make sure the initial dependencies and the Geoapify API key are imported.

4. From your `Vacation_Search` folder from Deliverable 2, import the `WeatherPy_vacation.csv` file as a DataFrame named `vacation_df`.

5. Use GeoViews to create a map that shows all the cities in the `vacation_df` DataFrame. Configure the map as follows:

    * The point's size should be the maximum temperature for the city

    * The point's color should be the city's name

    * Use the `hover_cols` parameter to the the "Hotel Name", "Country", and "Current Description" columns to each point as additional information.

6. From the map, *choose four cities* that a customer might want to visit. They should be close together and in the same country. Use the `loc` method to create separate DataFrames for each city on the travel route.

    > **Hint:** You will start and end the route in the same city, so the `vacation_start` and `vacation_end` DataFrames will be in the same city.

7. Use the Pandas `concat` function to merge the DataFrame from each city in the itinerary to create a new DataFrame named `itinerary_df` to store the itinerary details.

8. Use the Pandas `copy` function to create a new DataFrame named `waypoints_df` to store the longitude and latitude for each city in `itinerary_df`.

    > **Hint:** You'll use this DataFrame to create a map using GeoViews, so recall that the first column should be the longitude, and the second the latitude.

9. Use GeoViews to create a map that shows the four cities in the itinerary.

10. Next, you'll use the Geoapify Routing API to find a route between the cities in the itinerary. Review the code that sets the initial parameters and fetches the coordinates from each city to define the `waypoints` parameter by using a `for` loop.

    > **Hint:** You can note that the `mode` parameter is set to `drive`, you can play around with other modes as it's shown in [the "Travel modes" table](https://apidocs.geoapify.com/docs/routing/#api) in the Geoapify Routing API documentation.

11. Use the Geoapify Routing API to retrieve the route's directions for your itinerary.

12. From the JSON response, store the route's legs coordinates in a variable called `legs`.

13. Loop through the route legs coordinates to fetch the latitude and longitude for each step. Store the latitude and longitude values into two Python lists named `longitude` and `latitude`.

14. Use the `longitude` and `latitude` Python lists to create a new DataFrame named `route_df`.

15. Use the GeoViews `Path` function to configure a line plot by using `route_df`. Set a custom color and width for the line that may contrast with the map.

16. Use the asterisk operator to display a composed plot that shows the itinerary's route over the map containing the cities. 

17. Save your map to the `Vacation_Itinerary` folder as `WeatherPy_travel_map.png`.

---

## Make sure the initial dependencies and the Geoapify API key are imported

In [1]:
# Dependencies and Setup
import geoviews as gv
import hvplot.pandas
import pandas as pd
import requests

# Turn off warning messages
import warnings
warnings.filterwarnings("ignore")

# Import API key
from config import geoapify_key

## From your `Vacation_Search` folder from Deliverable 2, import the `WeatherPy_vacation.csv` file as a DataFrame named `vacation_df`

In [2]:
# Read the WeatherPy_vacation.csv into a DataFrame
vacation_df = pd.read_csv("../Vacation_Search/WeatherPy_vacation.csv")

# Display sample data
vacation_df.head()

Unnamed: 0          City Country  Max Temp Current Description      Lat  \
0           5       Rikitea      PF     78.55              Clouds -23.1203   
1          20     Bathsheba      BB     79.05              Clouds  13.2167   
2          29  Puerto Ayora      EC     78.55                Rain  -0.7393   
3          31        Namibe      AO     75.94              Clouds -15.1961   
4          32         Vaini      TO     80.80              Clouds -21.2000   

        Lng                            Hotel Name  
0 -134.9692                  Chez Bianca & Benoit  
1  -59.5167                        Atlantis Hotel  
2  -90.3518  Hostal La Mirada De Solitario George  
3   12.1522                Hotel Chik Chik Namibe  
4 -175.2000           Keleti International Resort

## Use GeoViews to create a map that shows all the cities in the `vacation_df` DataFrame. Configure the map as follows:

* The point's size should be the maximum temperature for the city

* The point's color should be the city's name

* Use the `hover_cols` parameter to the the "Hotel Name", "Country", and "Current Description" columns to each point as additional information.

In [3]:
# Configure the map plot
map_plot = vacation_df.hvplot.points(
    "Lng",
    "Lat",
    geo = True,
    tiles = "OSM",
    frame_width = 700,
    frame_height = 500,
    size = "Max Temp",
    scale = 1,
    color = "City",
    hover_cols = ["Hotel Name", "Country", "Current Description"]
)

#Display map
map_plot


:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (City,Max Temp,Hotel Name,Country,Current Description)

## From the map, *choose four cities* that a customer might want to visit. They should be close together and in the same country. Use the `loc` method to create separate DataFrames for each city on the travel route.

### Four cities in Indonesia

75	Pemangkat	ID	75.06	Rain	1.1667	108.9667	Hotel Kelapa Gading

120	Sibolga	ID	75.69	Rain	1.7427	98.7792	Hotel Prima Indah

135	Bengkulu	ID	76.21	Rain	-3.8004	102.2655	Dena Hotel

267	Banda Aceh	ID	76.01	Rain	5.5577	95.3222	Hotel 61


In [4]:
# Create DataFrames for each city by filtering the 'vacation_df' using the loc method
vacation_start = vacation_df.loc[(vacation_df["City"] =="Bengkulu")]
vacation_end = vacation_df.loc[(vacation_df["City"] =="Bengkulu")]
vacation_stop1 = vacation_df.loc[(vacation_df["City"] =="Sibolga")]
vacation_stop2 = vacation_df.loc[(vacation_df["City"] =="Bengkulu")]
vacation_stop3 = vacation_df.loc[(vacation_df["City"] =="Banda Aceh")]

vacation_stop3

Unnamed: 0        City Country  Max Temp Current Description     Lat  \
54         267  Banda Aceh      ID     76.01                Rain  5.5577   

        Lng Hotel Name  
54  95.3222   Hotel 61

## Use the Pandas `concat` function to merge the DataFrame from each city in the itinerary to create a new DataFrame named `itinerary_df` to store the itinerary details

In [5]:
# Use the Pandas concat function to create a new DataFrame to store the itinerary details.
itinerary_df = pd.concat([vacation_start, vacation_stop1,
                           vacation_stop2,vacation_stop3,
                           vacation_end], axis=0)
# Display sample data
itinerary_df

Unnamed: 0        City Country  Max Temp Current Description     Lat  \
26         135    Bengkulu      ID     76.21                Rain -3.8004   
24         120     Sibolga      ID     75.69                Rain  1.7427   
26         135    Bengkulu      ID     76.21                Rain -3.8004   
54         267  Banda Aceh      ID     76.01                Rain  5.5577   
26         135    Bengkulu      ID     76.21                Rain -3.8004   

         Lng         Hotel Name  
26  102.2655         Dena Hotel  
24   98.7792  Hotel Prima Indah  
26  102.2655         Dena Hotel  
54   95.3222           Hotel 61  
26  102.2655         Dena Hotel

## Use the Pandas `copy` function to create a new DataFrame named `waypoints_df` to store the longitude and latitude for each city in `itinerary_df`

In [6]:
# Create a Pandas DataFrame to store the latitude and longitude for each city in the itineray
waypoints_df = itinerary_df[['Lat', 'Lng']].copy()
# Display sample data
waypoints_df

Lat       Lng
26 -3.8004  102.2655
24  1.7427   98.7792
26 -3.8004  102.2655
54  5.5577   95.3222
26 -3.8004  102.2655

## Use GeoViews to create map that shows the four cities in the itinerary

In [7]:
# Configure the map plot by using the itineraty_df
waypoints_map  = waypoints_df.hvplot.points(
    "Lng",
    "Lat",
    geo = True,
    tiles = "OSM",
    frame_width = 500,
    frame_height = 300,
)


In [8]:
# Display the route_map
waypoints_map

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]

## Next, you'll use the Geoapify Routing API to find a route between the cities in the itinerary. Review the code that sets the initial parameters and fetches the coordinates from each city to define the `waypoints` parameter by using a `for` loop

In [9]:
# Set parameters to trace the route
radius = 5000
params = {
    "mode":"drive",
    "apiKey": geoapify_key,
}

In [10]:
# Set an empty waypoints String variable
waypoints = ""

# Iterate through the route_df DataFrame to define the waypoints
for index, row in waypoints_df.iterrows():
    waypoints = waypoints + str(row["Lat"]) + "," + str(row["Lng"]) + "|"

# Delete the last character from the string
waypoints = waypoints[:-1]

# Add the waypoints to the params dictionary
params["waypoints"] = waypoints

# Display the params dictionary
params

{'mode': 'drive',
 'apiKey': '487b47fb1d0a487cb2a2339b0271ac23',
 'waypoints': '-3.8004,102.2655|1.7427,98.7792|-3.8004,102.2655|5.5577,95.3222|-3.8004,102.2655'}

## Use the Geoapify Routing API to retrieve the route's directions for your itinerary

In [11]:
# Set up the base URL for the Geoapify Places API.
base_url = "https://api.geoapify.com/v1/routing"

# Make request and retrieve the JSON data by using the params dictionaty
route_response = requests.get(base_url, params = params)

# Convert the API response to JSON format
route_response = route_response.json()


## From the JSON response, store the route's legs coordinates in a variable called `legs`

In [20]:
# Fetch the route's legs coordinates from the JSON reponse
legs = route_response["features"][0]["geometry"]["coordinates"]
print(legs[1:3])

[[[98.779042, 1.743144], [98.779656, 1.743362], [98.780072, 1.742491], [98.780103, 1.742434], [98.78014, 1.742379], [98.780194, 1.742325], [98.780501, 1.742003], [98.780777, 1.741823], [98.781078, 1.741615], [98.781386, 1.741416], [98.781612, 1.741208], [98.781865, 1.741065], [98.782077, 1.740908], [98.782287, 1.740786], [98.782429, 1.740644], [98.782907, 1.740282], [98.783897, 1.739588], [98.784025, 1.739491], [98.7842, 1.739354], [98.784488, 1.739199], [98.784767, 1.73915], [98.784954, 1.73905], [98.785008, 1.738959], [98.785371, 1.738742], [98.785476, 1.738686], [98.785498, 1.738636], [98.7856, 1.738503], [98.785975, 1.738066], [98.786181, 1.73755], [98.786372, 1.737237], [98.78642, 1.737165], [98.786458, 1.737108], [98.786496, 1.737051], [98.786526, 1.737005], [98.786772, 1.736743], [98.787043, 1.736511], [98.787727, 1.735882], [98.787869, 1.735754], [98.788062, 1.735558], [98.788411, 1.735204], [98.788718, 1.734892], [98.788758, 1.734851], [98.78909, 1.734516], [98.789402, 1.7342]

## Loop through the route legs coordinates to fetch the latitude and longitude for each step. Store the latitude and longitude value into two Python lists names `longitude` and `latitude`

In [ ]:
# Create and empty list to store the longitude of each step
longitude = []

# Create and empty list to store the latitude of step
latitude = []

# Loop through the legs coordinates to fetch the latitude and longitude for each step

count = 1
for leg in legs:
    count += 1
    for coor in leg:
        longitude.append(coor[0])
        latitude.append(coor[1])

print(count)

In [ ]:
        
print("I got to here")    

print(latitude[1:3])

## Use the `longitude` and `latitude` Python lists to create a new DataFrame named `route_df`

In [ ]:
# Create an empty DataFrame to store the steps' coordinates
route_df = pd.DataFrame()

# Add the steps' longitude and latitude from each step as columns to the DataFrame
route_df['longitude'] = longitude
route_df['latitude'] = latitude

# Display sample data
route_df.head()

##  Use the GeoViews `Path` function to configure a line plot by using `route_df`. Set a custom color and width for the line that may contrast with the map

In [ ]:
# Configure the route path by using the GeoViews' Path function
route_path = gv.Path(
    route_df,
    ).opts(
    heigth = 500,
    width = 700,
    line_width = 3,
    color = "red"
)
route_path

In [ ]:
# Display a composed plot by using the route_map and route_path objects
map_plot